# Le groupe orthogonal de $\mathbb R^3$

Marc Lorenzi - juillet 2016

## 0 Préliminaires

On se place dans l'espace euclidien orienté $E=\mathbb R^3$. Les endomorphismes orthogonaux de $E$ sont de l'un des types suivants :
1. Les réflexions, symétries orthogonales par rapport à un plan, caractérisées par un vecteur normal au plan de la réflexion.
2. Les rotations. L'identité mise à part, elles sont caractérisées par un axe, orienté par un vecteur $e$, et un angle $\theta\not\equiv 0[2\pi]$.
3. Les composées d'une réflexion et d'une rotation différente de l'identité, dont l'axe est orthogonal au plan de la réflexion. L'axe et l'angle de la rotation caractérisent complètement ces endomorphismes orthogonaux.

On se propose de répondre aux deux questions suivantes :
1. Connaissant les éléments caractéristiques d'un endomorphisme orthogonal, déterminer sa matrice dans la base canonique.
2. Connaissant la matrice d'un endomorphisme orthogonal, déterminer sa nature et ses éléments caractéristiques.

In [ ]:
from sympy import *
init_printing()

Définissons tout d'abord les vecteurs de la base canonique de $\mathbb R^3$.

In [ ]:
e1 = Matrix([1, 0, 0])
e2 = Matrix([0, 1, 0])
e3 = Matrix([0, 0, 1])
e1, e2, e3

Et voici une petite fonction renvoyant un vecteur unitaire colinéaire à un vecteur non nul $u$.

In [ ]:
def normaliser(u):
    return u / u.norm()

In [ ]:
normaliser(Matrix([1, 2, 1]))

## 1 Les réflexions

### 1.1 Image d'un vecteur par une réflexion

Soit $f$ la réflexion de plan $P$, où $P$ est donné par un vecteur normal $e$. On a alors pour tout $u\in\mathbb R^3$, $f(u)=u-2\frac{<u,e>}{||e||^2}e$. 

In [ ]:
def reflexion(e, u):
    return u - 2 * u.dot(e) / e.norm() ** 2 * e

In [ ]:
reflexion(Matrix([1,1,1]), Matrix([1,2,1]))

### 1.2 Matrice d'une réflexion

Pour obtenir la matrice d'une réflexion, il suffit de calculer les images des vecteurs de la base canonique par celle-ci, puis de les ranger dans une matrice.

In [ ]:
def matrice_reflexion(e):
    u1 = reflexion(e, e1)
    u2 = reflexion(e, e2)
    u3 = reflexion(e, e3)
    return u1.col_insert(1, u2).col_insert(2, u3)

In [ ]:
A0 = matrice_reflexion(Matrix([1, 2, 3]))
A0

Quelques vérifications ... la matrice $A_0$ est symétrique, ce qui est une bonne chose. Ensuite,

In [ ]:
A0 * A0

et donc $A_0$ est une matrice de symétrie orthogonale. Enfin,

In [ ]:
det(A0)

donc $A_0$ est une matrice de réflexion.

### 1.3 Caractéristiques d'une réflexion

Donnons-nous une matrice $A$. La matrice $A$ est-elle une matrice de réflexion ? Et si oui, par rapport à quel plan ?

In [ ]:
def est_reflexion(A):
    return A != - eye(3) and A == A.T and A.T * A == eye(3) and det(A) == -1

In [ ]:
est_reflexion(A0)

In [ ]:
def analyse_reflexion(A):
    return (A + eye(3)).nullspace()[0]

In [ ]:
analyse_reflexion(A0)

## 2 Rotations

### 2.1 Image d'un vecteur par une rotation

Une rotation $f$ de l'espace différente de l'identité est caractérisée par son axe, orienté par un vecteur $\omega$ et son angle $\theta\not\equiv 0[2\pi]$. En prenant $\omega$ unitaire, on a pour tout vecteur $u$ de l'espace la formule d'Euler-Rodrigues :

$f(u)=\cos\theta u + <\omega, u> (1 - \cos\theta)\omega + \sin\theta\ \omega\land u$

La fonction __rotation__ renvoie l'image du vecteur u par la rotation caractérisée par $\omega$ unitaire et l'angle $\theta$.

In [ ]:
def rotation(omega, theta, u):
    c = cos(theta)
    s = sin(theta)
    v1 = c * u
    v2 = s * omega.cross(u)
    v3 = omega.dot(u) * (1 - c) * omega
    return v1 + v2 + v3

In [ ]:
x, y, z = symbols('x y z')

In [ ]:
rotation(normaliser(Matrix([1, 1, 1])), pi/2, Matrix([x, y, z]))

In [ ]:
simplify(_)

Pour obtenir la matrice de la rotation, il suffit de calculer les images des vecteurs de la base canonique par celle-ci.

In [ ]:
def matrice_rotation(omega, theta):
    omega = normaliser(omega)
    u = rotation(omega, theta, e1)
    v = rotation(omega, theta, e2)
    w = rotation(omega, theta, e3)
    return u.col_insert(1, v).col_insert(2, w)

In [ ]:
A = matrice_rotation(Matrix([1, 1, 1]), pi / 2)
A

### 2.2 Déterminer les caractéristiques d'une rotation

Il est facile de savoir si une matrice $A$ est la matrice d'une rotation différente de l'identité.

In [ ]:
def est_rotation(A):
    return simplify(A.T * A) == eye(3) and A != eye(3) and simplify(det(A)) == 1

L'axe de la rotation est l'ensemble des invariants.

In [ ]:
def invariants(A):
    return (A - eye(3)).nullspace()[0]

In [ ]:
invariants(A)

In [ ]:
e=simplify(_)
e

Le cosinus de l'angle est donné par la trace de la rotation : $Tr\ A = 1 + 2\cos\theta$. 

In [ ]:
def cos_angle(A):
    return (A.trace() - 1) / 2

In [ ]:
cos_angle(A)

Pour obtenir le signe du sinus, on prend un vecteur $u$ qui n'est pas sur l'axe et on calcule le déterminant de $u,f(u),e$ où $e$ est un vecteur qui dirige l'axe (pas forcément unitaire). Le signe de $\sin\theta$ est alors le signe de ce daterminant.

In [ ]:
def signe_sin_angle(A, e):
    if e.cross(Matrix([1, 0, 0])) != 0:
        u = Matrix([1, 0, 0])
    else:
        u = Matrix([0, 1, 0])
    v = A * u
    M = Matrix([u.T, v.T, e.T]).T
    return M.det()

In [ ]:
signe_sin_angle(A, e)

On regroupe le tout en une seule fonction. La fonction __analyse_rotation__ prend en paramètre une matrice $A$ censée être une matrice de rotation différente de l'identité. Elle renvoie le couple $(e,\theta)$ où $e$ est un vecteur de l'axe (pas nécessairement unitaire) et $\theta$ est l'angle de la rotation.

In [ ]:
def analyse_rotation(A):
    e = simplify(invariants(A))
    c = cos_angle(A)
    theta = acos(c)
    s = signe_sin_angle(A, e)
    if s >= 0: return (e, theta)
    else: return (e, -theta)

In [ ]:
analyse_rotation(A)

Essayons deux autres exemples.

In [ ]:
A2 = Matrix([[3, 1, sqrt(6)],[1, 3, -sqrt(6)],[-sqrt(6),sqrt(6), 2]])/4
A2

In [ ]:
est_rotation(A2)

In [ ]:
analyse_rotation(A2)

In [ ]:
A3 = Matrix([[8,1,-4],[-4,4,-7],[1,8,4]])/9
A3

In [ ]:
est_rotation(A3)

In [ ]:
analyse_rotation(A3)

Remarquons pour terminer que l'identité, qui est une rotation, n'a pas d'axe défini de façon unique. Cela dit, notre fonction renvoie des résultats tout à fait logiques.

In [ ]:
analyse_rotation(eye(3))

## 3 Composée d'une réflexion et d'une rotation

Soit $f$ un endomorphisme orthogonal de l'espace qui n'est ni ni une rotation ni une réflexion et qui est différent de $-id$. Alors $f$ s'crit de façon unique $g\circ h$ où $g$ est une rotation différente de l'identité, $h$ est une réflexion, et le plan de la réflexion $h$ est orthogonal à l'axe de la rotation $g$. De plus, $g$ et $h$ commutent.

Pour obtenir les caractéristiques de $f$, on cherche tout d'abord l'ensemble $D$ des vecteurs changés en leur opposé. Ce sera l'axe de $g$. On oriente $D$ par un vecteur $e$. Le plan de $h$ est alors l'orthogonal de $e$ et $h$ est complètement déterminée. Comme $f = g\circ h$, on a aussi $g = f\circ h$ et la détermination de $g$ est alors facile.

In [ ]:
def analyse_reflex_rot(A):
    e = (A + eye(3)).nullspace()[0]
    B = matrice_reflexion(e) * A
    (e1, theta) = analyse_rotation(B)
    return (e, theta)

Prenons l'une des matrices de rotation vues ci-dessus et prenons l'opposé de sa première colonne.

In [ ]:
A4 = Matrix([[-3, 1, sqrt(6)],[-1, 3, -sqrt(6)],[sqrt(6),sqrt(6), 2]])/4
A4

In [ ]:
e, theta = analyse_reflex_rot(A4)

In [ ]:
e

In [ ]:
theta

Vérifications ...

In [ ]:
matrice_reflexion(e) * matrice_rotation(e, theta)

In [ ]:
matrice_rotation(e, theta) * matrice_reflexion(e)

On retrouve bien la matrice $A_4$, ceci quel que soit le sens dans lequel on effectue les produits.

In [ ]:
analyse_rotation(Matrix([[1,0,0],[0,1,0],[0,0,1]]))

Remarquons pour terminer que $-id$ se décompose aussi comme un produit de réflexion et de rotation, mais on n'a plus unicité.

In [ ]:
analyse_reflex_rot(-eye(3))

## 4 Regroupons le tout

In [ ]:
def analyse(A):
    if simplify(A * A.T) != eye(3):
        return (0, [])
    elif est_reflexion(A):
        return (1, analyse_reflexion(A))
    elif est_rotation(A):
        return (2, analyse_rotation(A))
    else:
        return (3, analyse_reflex_rot(A))

In [ ]:
analyse(A)

In [ ]:
analyse(A4)

In [ ]:
analyse(A0)

In [ ]:
analyse(2*eye(3))